In [23]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import folium
from folium.plugins import HeatMap, HeatMapWithTime
import io
from PIL import Image
import json
from branca.colormap import LinearColormap


In [2]:
df = pd.read_csv('/Users/los/Documents/King-County-Washington-Regression-Analysis/data/cleaned_2.csv')

In [3]:
df2 =pd.read_csv('/Users/los/Documents/King-County-Washington-Regression-Analysis/data/kc_house_data.csv')

In [4]:
df.drop(['Unnamed: 0'], axis=1,inplace =True)

In [5]:
f = open('/Users/los/Documents/King-County-Washington-Regression-Analysis/Notebooks/Zipcodes_for_King_County_and_Surrounding_Area___zipcode_area.geojson')
data = json.load(f)


In [6]:
df.head()

id        date     price  bedrooms  bathrooms  sqft_living  \
0  7129300520  2014-10-13  221900.0         3       1.00         1180   
1  6414100192  2014-12-09  538000.0         3       2.25         2570   
2  5631500400  2015-02-25  180000.0         2       1.00          770   
3  2487200875  2014-12-09  604000.0         4       3.00         1960   
4  1954400510  2015-02-18  510000.0         3       2.00         1680   

   sqft_lot  floors  waterfront  view  ...  sqft_basement  yr_built  \
0      5650     1.0           0   1.0  ...            0.0      1955   
1      7242     2.0           0   1.0  ...          400.0      1951   
2     10000     1.0           0   1.0  ...            0.0      1933   
3      5000     1.0           0   1.0  ...          910.0      1965   
4      8080     1.0           0   1.0  ...            0.0      1987   

   yr_renovated  zipcode      lat     long  sqft_living15  sqft_lot15  \
0             0    98178  47.5112 -122.257           1340        5650   
1          1991    98125  47.7210 -122.319           1690        7639   
2             0    98028  47.7379 -122.233           2720        8062   
3             0    98136  47.5208 -122.393           1360        5000   
4             0    98074  47.6168 -122.045           1800        7503   

   year_sold  month_sold  
0       2014          10  
1       2014          12  
2       2015           2  
3       2014          12  
4       2015           2  

[5 rows x 23 columns]

In [7]:
df2.head()

id        date     price  bedrooms  bathrooms  sqft_living  \
0  7129300520  10/13/2014  221900.0         3       1.00         1180   
1  6414100192   12/9/2014  538000.0         3       2.25         2570   
2  5631500400   2/25/2015  180000.0         2       1.00          770   
3  2487200875   12/9/2014  604000.0         4       3.00         1960   
4  1954400510   2/18/2015  510000.0         3       2.00         1680   

   sqft_lot  floors waterfront  view  ...          grade sqft_above  \
0      5650     1.0        NaN  NONE  ...      7 Average       1180   
1      7242     2.0         NO  NONE  ...      7 Average       2170   
2     10000     1.0         NO  NONE  ...  6 Low Average        770   
3      5000     1.0         NO  NONE  ...      7 Average       1050   
4      8080     1.0         NO  NONE  ...         8 Good       1680   

   sqft_basement yr_built  yr_renovated  zipcode      lat     long  \
0            0.0     1955           0.0    98178  47.5112 -122.257   
1          400.0     1951        1991.0    98125  47.7210 -122.319   
2            0.0     1933           NaN    98028  47.7379 -122.233   
3          910.0     1965           0.0    98136  47.5208 -122.393   
4            0.0     1987           0.0    98074  47.6168 -122.045   

   sqft_living15  sqft_lot15  
0           1340        5650  
1           1690        7639  
2           2720        8062  
3           1360        5000  
4           1800        7503  

[5 rows x 21 columns]

In [8]:
lan_long = df[['lat','long','price']]
lan_long.sample(1000)
lan_long_2 =df[['lat','long','zipcode']]

In [10]:
merged_df = pd.merge(lan_long, lan_long_2[['lat', 'long', 'zipcode']], on=['lat', 'long'])
merged_df

lat     long      price  zipcode
0      47.5112 -122.257   221900.0    98178
1      47.7210 -122.319   538000.0    98125
2      47.7379 -122.233   180000.0    98028
3      47.5208 -122.393   604000.0    98136
4      47.6168 -122.045   510000.0    98074
...        ...      ...        ...      ...
17428  47.5137 -122.167   610685.0    98056
17429  47.5537 -122.398  1010000.0    98136
17430  47.5107 -122.362   400000.0    98146
17431  47.5944 -122.299   402101.0    98144
17432  47.5941 -122.299   325000.0    98144

[17433 rows x 4 columns]

In [14]:
mapping = folium.Map(location=[merged_df['lat'].mean(), merged_df['long'].mean()], zoom_start=10, detect_retina=True, control_scale=False, tiles='Stamen Terrain')
gradient = {0.2: 'blue', 0.4: 'green', 0.6: 'orange', 1: 'red'}


In [16]:
max_price = merged_df['price'].max()
merged_df['normalized_price'] = merged_df['price'] / max_price
merged_df

lat     long      price  zipcode  normalized_price
0      47.5112 -122.257   221900.0    98178          0.143161
1      47.7210 -122.319   538000.0    98125          0.347097
2      47.7379 -122.233   180000.0    98028          0.116129
3      47.5208 -122.393   604000.0    98136          0.389677
4      47.6168 -122.045   510000.0    98074          0.329032
...        ...      ...        ...      ...               ...
17428  47.5137 -122.167   610685.0    98056          0.393990
17429  47.5537 -122.398  1010000.0    98136          0.651613
17430  47.5107 -122.362   400000.0    98146          0.258065
17431  47.5944 -122.299   402101.0    98144          0.259420
17432  47.5941 -122.299   325000.0    98144          0.209677

[17433 rows x 5 columns]

In [ ]:
heat_data = [[row['lat'], row['long'], row['normalized_price'], row['zipcode']] for index, row in merged_df.iterrows()]

In [21]:
HeatMap(heat_data, min_opacity=0.5, blur=3, radius=2, gradient=gradient).add_to(folium.FeatureGroup(name='Heat Map').add_to(mapping))
display(mapping)


In [30]:
# Merging the 'lan_long' and 'lan_long_2' DataFrames on 'lat' and 'long' to get 'price' and 'zipcode'
merged_df = pd.merge(df[['lat', 'long', 'price']], df[['lat', 'long', 'zipcode']], on=['lat', 'long'])

# Create a Folium map with a starting zoom level of 11
mapping = folium.Map(location=[merged_df['lat'].mean(), merged_df['long'].mean()], zoom_start=11, detect_retina=True, control_scale=False, tiles='Stamen Terrain')

# Normalize the housing prices between 0 and 1 for the heatmap
max_price = merged_df['price'].max()
merged_df['normalized_price'] = merged_df['price'] / max_price

# Convert the DataFrame to a list of lists (required for HeatMap)
heat_data = [[row['lat'], row['long'], row['normalized_price']] for index, row in merged_df.iterrows()]

# Define a custom gradient color scheme for the heatmap with darker colors
gradient = {
    0.0: 'darkblue',    # Lowest normalized price
    0.2: 'darkgreen',
    0.4: 'darkorange',
    1.0: 'darkred'      # Highest normalized price
}

# Add the HeatMap layer to the map with the custom gradient color scheme
HeatMap(heat_data, min_opacity=0.5, blur=3, radius=2, gradient=gradient).add_to(folium.FeatureGroup(name='Heat Map').add_to(mapping))

# Add LayerControl to the map
folium.LayerControl().add_to(mapping)

# Display the map
display(mapping)
